In [38]:
import warnings
warnings.filterwarnings("ignore")

import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from scipy import stats

import pandas_profiling

In [2]:
df = pd.read_csv('Churn_Modelling.csv')
df.head(3)

RowNumber  CustomerId   Surname  CreditScore Geography  Gender  Age  \
0          1    15634602  Hargrave          619    France  Female   42   
1          2    15647311      Hill          608     Spain  Female   41   
2          3    15619304      Onio          502    France  Female   42   

   Tenure    Balance  NumOfProducts  HasCrCard  IsActiveMember  \
0       2       0.00              1          1               1   
1       1   83807.86              1          0               1   
2       8  159660.80              3          1               0   

   EstimatedSalary  Exited  
0        101348.88       1  
1        112542.58       0  
2        113931.57       1

### Let's check out a newly found tool, profiling.

In [4]:
pandas_profiling.ProfileReport(df)

### A few notes after taking a look at this:

### There are a lot of people with no balance.  Let's run a chi test later to compare the churn rate of this group to the churn rate of the whole dataset.

### This is a fairly small percentage for customers that left.  We need to make sure we stratify on 'Exited'.

### Hypotheses:

### - Customers with no balance will churn at a higher rate than those with a balance.
#### - 24.5% of customers that churned had no balance.

### - Customers with lower credit score may churn more.
#### -- Customers that exit do have a slightly lower credit score, but not a significant difference.

### - Customers with credit cards will churn less.  This might be the result of them having to still make payments on their balance.
#### -- These percentages are almost identical.  Having a credit card does not seem important.

### - Inactive customers may churn more than active. 
#### -- Noted below, of those that exited, 63.9% were non-active vs. 44.5% non-active in the customers that did not exit.

In [15]:
df[(df.Balance == 0) & (df.Exited == 1)]['CustomerId'].count()

500

In [16]:
df[(df.Balance > 0) & (df.Exited == 1)]['CustomerId'].count()

1537

In [13]:
df[df.Exited == 1].describe()

RowNumber    CustomerId  CreditScore          Age       Tenure  \
count  2037.000000  2.037000e+03  2037.000000  2037.000000  2037.000000   
mean   4905.917526  1.569005e+07   645.351497    44.837997     4.932744   
std    2866.855245  7.269262e+04   100.321503     9.761562     2.936106   
min       1.000000  1.556571e+07   350.000000    18.000000     0.000000   
25%    2419.000000  1.562736e+07   578.000000    38.000000     2.000000   
50%    4871.000000  1.568896e+07   646.000000    45.000000     5.000000   
75%    7404.000000  1.575309e+07   716.000000    51.000000     8.000000   
max    9999.000000  1.581566e+07   850.000000    84.000000    10.000000   

             Balance  NumOfProducts    HasCrCard  IsActiveMember  \
count    2037.000000    2037.000000  2037.000000     2037.000000   
mean    91108.539337       1.475209     0.699067        0.360825   
std     58360.794816       0.801521     0.458776        0.480358   
min         0.000000       1.000000     0.000000        0.000000   
25%     38340.020000       1.000000     0.000000        0.000000   
50%    109349.290000       1.000000     1.000000        0.000000   
75%    131433.330000       2.000000     1.000000        1.000000   
max    250898.090000       4.000000     1.000000        1.000000   

       EstimatedSalary  Exited  
count      2037.000000  2037.0  
mean     101465.677531     1.0  
std       57912.418071     0.0  
min          11.580000     1.0  
25%       51907.720000     1.0  
50%      102460.840000     1.0  
75%      152422.910000     1.0  
max      199808.100000     1.0

### Above is the summary of customers that churned.

### Below is the summary of customers that did not churn.

In [14]:
df[df.Exited == 0].describe()

RowNumber    CustomerId  CreditScore          Age       Tenure  \
count   7963.000000  7.963000e+03  7963.000000  7963.000000  7963.000000   
mean    5024.694964  1.569117e+07   651.853196    37.408389     5.033279   
std     2891.682053  7.174423e+04    95.653837    10.125363     2.880658   
min        2.000000  1.556570e+07   405.000000    18.000000     0.000000   
25%     2526.500000  1.562882e+07   585.000000    31.000000     3.000000   
50%     5042.000000  1.569154e+07   653.000000    36.000000     5.000000   
75%     7525.500000  1.575335e+07   718.000000    41.000000     7.000000   
max    10000.000000  1.581569e+07   850.000000    92.000000    10.000000   

             Balance  NumOfProducts    HasCrCard  IsActiveMember  \
count    7963.000000    7963.000000  7963.000000     7963.000000   
mean    72745.296779       1.544267     0.707146        0.554565   
std     62848.040701       0.509536     0.455101        0.497045   
min         0.000000       1.000000     0.000000        0.000000   
25%         0.000000       1.000000     0.000000        0.000000   
50%     92072.680000       2.000000     1.000000        1.000000   
75%    126410.280000       2.000000     1.000000        1.000000   
max    221532.800000       3.000000     1.000000        1.000000   

       EstimatedSalary  Exited  
count      7963.000000  7963.0  
mean      99738.391772     0.0  
std       57405.586966     0.0  
min          90.070000     0.0  
25%       50783.490000     0.0  
50%       99645.040000     0.0  
75%      148609.955000     0.0  
max      199992.480000     0.0

### A few notes from above:

### Credit score does not seem to be a big difference.  Customers that churn appear to be slightly older.  There are plenty of customers that don't churn that have no balance.

In [17]:
pandas_profiling.ProfileReport(df[df.Exited == 1])

### Above is the profiling for customers that churned and below is the profiling for customers that did not churn.

In [18]:
pandas_profiling.ProfileReport(df[df.Exited == 0])

In [28]:
pd.DataFrame((df.groupby(['Exited', 'IsActiveMember'])['Balance'].count())/(df.groupby('Exited')['Balance'].count()))

Balance
Exited IsActiveMember          
0      0               0.445435
       1               0.554565
1      0               0.639175
       1               0.360825

In [32]:
pd.DataFrame((df.groupby(['HasCrCard', 'Exited'])['CreditScore'].mean()))

CreditScore
HasCrCard Exited             
0         0        652.425815
          1        647.234910
1         0        651.616054
          1        644.540730

In [36]:
pd.DataFrame((df.groupby(['HasCrCard', 'Exited'])['CreditScore'].count())/(df.groupby('HasCrCard')['CreditScore'].count()))

CreditScore
HasCrCard Exited             
0         0          0.791851
          1          0.208149
1         0          0.798157
          1          0.201843

In [37]:
pd.DataFrame((df.groupby('Exited')['Balance'].mean()))

Balance
Exited              
0       72745.296779
1       91108.539337

In [39]:
crosstab = pd.crosstab(df['Exited'], df['HasCrCard'])
stat

HasCrCard     0     1
Exited               
0          2332  5631
1           613  1424